In [1]:
import numpy as np
from numba import njit
from functools import partial

import talib 
import pandas as pd
import vectorbt as vbt
import vectorbt as vbt
from vectorbt.utils.colors import adjust_opacity
from vectorbt.utils.enum_ import map_enum_fields
from vectorbt.base.reshape_fns import broadcast, flex_select_auto_nb, to_2d_array
from vectorbt.portfolio.enums import SizeType, Direction, NoOrder, OrderStatus, OrderSide
from vectorbt.portfolio import nb

import sys
import os
function_essential_path = r"C:\Users\Jordi\Desktop\Environement de developement\Trading_Dev_Stratégie_Environement\FunctionEssential"
function_s_score_path = r'C:\Users\Jordi\Desktop\Environement de developement\Trading_Dev_Stratégie_Environement\Indicateur'
sys.path.append(function_essential_path)
sys.path.append(function_s_score_path)
import utils as us
import s_score as score

In [47]:

def entries_trades(close, s_score_ajusted, adx, seuil,seuil_adx):
    entries_long = [False] * len(close)
    entries_short = [False] * len(close)


    for i in range(len(close)):

        if s_score_ajusted[i] >= seuil:
            for j in range(i, len(close) - 1):
                if s_score_ajusted[j] > s_score_ajusted[j + 1]:
                    if (adx.iloc[j+1] > seuil_adx):
                        break
                    else:
                        entries_short[j+1] = True
                        break

        if s_score_ajusted[i] <= -1 * seuil:
            for j in range(i, len(close) - 1):
                if s_score_ajusted[j] < s_score_ajusted[j + 1]:
                    if (adx.iloc[j+1] > seuil_adx):
                        break
                    else:
                        entries_long[j+1] = True
                        break

    return entries_long, entries_short


In [64]:
##CLASS STRATEGIE##

@njit
def pre_sim_func_nb(c):
    entry_price = np.full(c.target_shape[1], np.nan, dtype=np.float64)  
    return (entry_price,)

@njit
def order_func_nb(c, entry_price, long, short, stop_loss, take_profit, size):
    price_now = nb.get_elem_nb(c, c.close)
    entry_long_now = nb.get_elem_nb(c, long)
    entry_short_now = nb.get_elem_nb(c, short)

    if entry_long_now:
        if c.position_now == 0:
            return nb.order_nb(
                size[c.col], 
                price=price_now,
                direction=Direction.LongOnly,
                fees=0.001
            )
        elif c.position_now < 0:
            return nb.order_nb(
                -size[c.col],  
                price=price_now,
                direction=Direction.ShortOnly,
                fees=0.0005
            )  

    if entry_short_now:
        if c.position_now == 0:
            return nb.order_nb(
                size[c.col], 
                price=price_now,
                direction=Direction.ShortOnly,
                fees=0.001
            )
        elif c.position_now > 0:
            return nb.order_nb(
                -size[c.col],  
                price=price_now,
                direction=Direction.LongOnly,
                fees=0.0005
            )

    if c.position_now > 0:
        SL = entry_price[c.col] * (1 - stop_loss[c.col])
        TP = entry_price[c.col] * (1 + take_profit[c.col])
        
        if price_now >= TP:
            return nb.order_nb(
                -size[c.col],
                price=TP,
                direction=Direction.LongOnly,
                fees=0.0005
            )
        elif price_now <= SL:
            return nb.order_nb(
                -size[c.col],
                price=SL,
                direction=Direction.LongOnly,
                fees=0.0005
            )

    if c.position_now < 0:
        SL = entry_price[c.col] * (1 + stop_loss[c.col])
        TP = entry_price[c.col] * (1 - take_profit[c.col])
        
        if price_now >= SL:
            return nb.order_nb(
                -size[c.col],
                price=SL,
                direction=Direction.ShortOnly,
                fees=0.0005
            )
        elif price_now <= TP:
            return nb.order_nb(
                -size[c.col],
                price=TP,
                direction=Direction.ShortOnly,
                fees=0.0005
            )

    return NoOrder

@njit
def post_order_func_nb(c, entry_price):
    if c.order_result.status == OrderStatus.Filled:
        entry_price[c.col] = c.order_result.price

class Strategie():


    def __init__(self,data,tickers,frequence_exec,frequence,multitimeframe):
        self.data = data
        self.tickers = tickers
        self.frequence_exec = frequence_exec
        self.frequences = frequence
        self.multitimeframe = multitimeframe   ## Si 0 pas de multitimeframe si 1 multitimeframe

    def backtest(self,sscore):
        entries_long_df = pd.DataFrame()
        entries_short_df = pd.DataFrame()
        exits_long_df = pd.DataFrame()
        exits_short_df = pd.DataFrame()
        close_df = pd.DataFrame()
        datetime_df = pd.DataFrame()

        for ticker in self.tickers:
            data = self.data[ticker]
            datetime = data.reset_index()['Datetime']
            s_score_ajuster = sscore[ticker]['adjusted_s_scores_vol']
            adx = talib.ADX(data['high'], data['low'], data['close'], timeperiod=50)
            long,short = entries_trades(data['close'],s_score_ajuster,adx,3,25)
            long = pd.Series(long, index=data['close'].index)
            short = pd.Series(short, index=data['close'].index)

            us.print_trades(0,long,short,None,None,data)
           
            long = long.reset_index(drop=True)
            short = short.reset_index(drop=True)
            close = data['close'].reset_index(drop=True)
            datetime = datetime.reset_index(drop=True)
            entries_long_df[ticker] = long
            entries_short_df[ticker] = short
            close_df[ticker] = close
            datetime_df[ticker] = datetime
        




        capital = 100000  
        risk_per_trade = 0.01  
        position_value = capital * risk_per_trade  

        size = np.array([(0.01 * capital) / (0.02 * close_df.iloc[0, i]) for i in range(len(self.tickers))])


        stop_loss = np.array([0.02] * len(self.tickers))  
        take_profit = np.array([0.04] * len(self.tickers))  

        portfolio = vbt.Portfolio.from_order_func(
            close_df,  
            order_func_nb,  
            entries_long_df.values,  
            entries_short_df.values,  
            stop_loss,  
            take_profit,  
            size,  
            freq=self.frequence_exec,  
            init_cash=100000,  # Ajout du capital initial
            pre_sim_func_nb=pre_sim_func_nb,  
            post_order_func_nb=post_order_func_nb,  
            broadcast_named_args=dict(  
                long=entries_long_df.values,  
                short=entries_short_df.values,  
                stop_loss=stop_loss,  
                take_profit=take_profit,  
                size=size  
            )
        )


        us.rapport_backtest(portfolio,close_df,datetime_df,self.tickers)

        return portfolio


In [62]:
tickers = ['USDJPY','GPDUSD','EURUSD']
DATA = us.get_data_forex(tickers,'H4',"2000-01-01","2011-01-01")
s_score_value = {}
for ticker in tickers:
    data_traitement = DATA[ticker]
    nb_nan = data_traitement['close'].isna().sum()
    close = data_traitement['close'].dropna()
    close_without_index = close.reset_index()
    result = score.mean_reversion(close, close_without_index['Datetime'], 85, "VOL", 0.5, "EGARCH")
    result_df = pd.DataFrame({
        's_score_value': result[0],
        'adjusted_s_scores_vol': result[1],
        'theta_vals': result[2],
        'mu_vals': result[3],
        'sigma_vals': result[4]
    })
    nan_rows = pd.DataFrame([[float('nan')] * result_df.shape[1]] * nb_nan, columns=result_df.columns)
    result_df = pd.concat([result_df, nan_rows], ignore_index=True)

    s_score_value[ticker] = result_df

Estimation des paramètres OU:   0%|          | 0/13191 [00:00<?, ?it/s]

  0%|          | 0/13191 [00:00<?, ?it/s]

C:\Users\Jordi\Desktop\Environement de developement\Trading_Dev_Stratégie_Environement\Indicateur\s_score.py:31: RuntimeWarning:

invalid value encountered in sqrt

c:\Users\Jordi\AppData\Local\Programs\Python\Python312\Lib\site-packages\arch\univariate\base.py:768: ConvergenceWarning:

The optimizer returned code 4. The message is:
Inequality constraints incompatible
See scipy.optimize.fmin_slsqp for code meaning.


Calcul de la volatilité conditionnelle: 100%|██████████| 13276/13276 [00:00<00:00, 286173.19it/s]
C:\Users\Jordi\AppData\Local\Temp\ipykernel_23136\1106309035.py:18: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



13275


  0%|          | 0/13188 [00:00<?, ?it/s]

...

13272


Estimation des paramètres OU:   0%|          | 0/13184 [00:00<?, ?it/s]

  0%|          | 0/13184 [00:00<?, ?it/s]

Estimation des paramètres OU:   0%|          | 0/13188 [00:10<?, ?it/s]
C:\Users\Jordi\Desktop\Environement de developement\Trading_Dev_Stratégie_Environement\Indicateur\s_score.py:31: RuntimeWarning:

invalid value encountered in sqrt

c:\Users\Jordi\AppData\Local\Programs\Python\Python312\Lib\site-packages\arch\univariate\base.py:768: ConvergenceWarning:

The optimizer returned code 4. The message is:
Inequality constraints incompatible
See scipy.optimize.fmin_slsqp for code meaning.


Calcul de la volatilité conditionnelle: 100%|██████████| 13269/13269 [00:00<00:00, 230690.11it/s]

13268


In [65]:
strat = Strategie(DATA,tickers,"240m","240m",0)
portfolio = strat.backtest(s_score_value)


---------------------------------------------------------------GLOBAL EQUITY CURVE---------------------------------------------------------------




------------------------------------------------------------------GLOBAL METRICS-----------------------------------------------------------------


------------------------------------------------------------------DETAILS : USDJPY-----------------------------------------------------------------

Total Return : -2.35%
Benchmark return : -34.96%
CAGR : -0.39%
Volatility : 3.37%
Sharpe Ratio : -0.1
Benchmark sharpe ratio : -0.2
Max Drawdown: -10.74%
Calmar Ratio : -0.04
Beta : -0.0


Total trades : 47
Total long trades 22
Total short trades 25
Win rate : 0.43%
Wining streak : 4.0
Loosing streak : 5.0
Average winning trade : 3.0%
Average losing trade : -2.0%
Profit factor : 0.9
Expectancy : -49.92%



 -> Average duration trades (jour) : 29.21




--------------------------------------------------------------------------------------------------------------------------------------------------


------------------------------------------------------------------DETAILS : GPDUSD-----------------------------------------------------------------

Total Return : 4.97%
Benchmark return : 0.74%
CAGR : 0.8%
Volatility : 3.48%
Sharpe Ratio : 0.25
Benchmark sharpe ratio : 0.03
Max Drawdown: -10.88%
Calmar Ratio : 0.07
Beta : -0.0


Total trades : 33
Total long trades 14
Total short trades 19
Win rate : 0.45%
Wining streak : 4.0
Loosing streak : 8.0
Average winning trade : 3.0%
Average losing trade : -2.0%
Profit factor : 1.23
Expectancy : 150.5%



 -> Average duration trades (jour) : 35.88




--------------------------------------------------------------------------------------------------------------------------------------------------


------------------------------------------------------------------DETAILS : EURUSD-----------------------------------------------------------------

Total Return : 13.62%
Benchmark return : 37.21%
CAGR : 2.13%
Volatility : 4.06%
Sharpe Ratio : 0.54
Benchmark sharpe ratio : 0.2
Max Drawdown: -5.03%
Calmar Ratio : 0.42
Beta : -0.04


Total trades : 31
Total long trades 13
Total short trades 18
Win rate : 0.48%
Wining streak : 3.0
Loosing streak : 4.0
Average winning trade : 3.0%
Average losing trade : -2.0%
Profit factor : 1.66
Expectancy : 439.3%



 -> Average duration trades (jour) : 34.63




--------------------------------------------------------------------------------------------------------------------------------------------------



In [36]:
portfolio.plot(column='USDJPY').show()

C:\Users\Jordi\AppData\Local\Temp\ipykernel_23136\3205677915.py:1: UserWarning:

Subplot 'trade_pnl' raised an exception

Estimation des paramètres OU:   0%|          | 0/36224 [08:47<?, ?it/s]


ValueError: 
    Invalid element(s) received for the 'opacity' property of scatter.marker
        Invalid elements include: [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]

    The 'opacity' property is a number and may be specified as:
      - An int or float in the interval [0, 1]
      - A tuple, list, or one-dimensional numpy array of the above